<h1 align=center><font size = 6>The Battle of Neighborhoods (Week 1)</font></h1>

##  Introduction/Business Problem

Clearly define a problem or an idea of your choice, where you would need to leverage the Foursquare location data to solve or execute. Remember that data science problems always target an audience and are meant to help a group of stakeholders solve a problem, so make sure that you explicitly describe your audience and why they would care about your problem.

This submission will eventually become your Introduction/Business Problem section in your final report. So I recommend that you push the report (having your Introduction/Business Problem section only for now) to your Github repository and submit a link to it.

### Cloud Kitchen in City of Toronto

1.	A description of the problem and a discussion of the background

A client is interested in setting up cloud kitchen in the city of Toronto. A cloud kitchen is a restaurant
that has no physical space and no dine-in or takeaway facility as it does not exist as a restaurant of
any sort. It relies entirely on third-party integrations or home delivery orders placed on call through
a website or an app. This format gives the restaurant the flexibility to more than one brand using the
same kitchen infrastructure.
The restaurateur (client) currently owns an Iranian restaurant. He would also like to serve Lebanese
and Egyptian cuisine to his customers under a different brand name. A cloud kitchen will enable this
business quite perfectly and the client is looking for a perfect location in Toronto to start his cloud
kitchen.
The target audience is the restaurant owner who is looking for a suitable location in the big city of
Toronto. He is looking to leverage his existing business and expand through cloud kitchen. By
providing recommendation for a suitable location, the client will be able to ideally build his cloud
kitchen to expand his business. 


## Data section

Describe the data that you will be using to solve the problem or execute your idea. Remember that you will need to use the Foursquare location data to solve the problem or execute your idea. You can absolutely use other datasets in combination with the Foursquare location data. So make sure that you provide adequate explanation and discussion, with examples, of the data that you will be using, even if it is only Foursquare location data.

This submission will eventually become your Data section in your final report. So I recommend that you push the report (having your Data section) to your Github repository and submit a link to it.


2.	A description of the data and how it will be used to solve the problem

We will use the Notebook to build the code to scrape the following Wikipedia
page, https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M, in order to obtain the
data that is in the table of postal codes and to transform the data into a pandas dataframe.

 The dataframe will consist of three columns: Postal Code, Borough, and Neighborhood

 The data will then be divided into different boroughs which will be further divided into
neighborhoods.

 Foursquare API will then be used to retrieve restaurant data of Toronto city.

 Using data analysis techniques that have been acquired over the last few months, three perfect
locations to setup a cloud kitchen will be recommended to the client.

 The recommendation will be based on below criteria:

o Number of competing restaurants in a particular neighborhood
o Proximity to residential areas
o Optimal location in terms of real estate cost (Additional data will be required for this criteria)

 Conclude three best location for a cloud kitchen in Toronto serving Iranian, Lebanese and
Egyptian cuisine

<h1 align=center><font size = 6>The Battle of Neighborhoods (Week 2)</font></h1>

For the second week, the final deliverables of the project will be:

A link to your Notebook on your Github repository, showing your code. (15 marks)
A full report consisting of all of the following components (15 marks):
Introduction where you discuss the business problem and who would be interested in this project.
Data where you describe the data that will be used to solve the problem and the source of the data.
Methodology section which represents the main component of the report where you discuss and describe any exploratory data analysis that you did, any inferential statistical testing that you performed, if any, and what machine learnings were used and why.
Results section where you discuss the results.
Discussion section where you discuss any observations you noted and any recommendations you can make based on the results.
Conclusion section where you conclude the report.
3. Your choice of a presentation or blogpost. (10 marks)

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2019.11.28 |       hecc5488_0         145 KB  conda-forge
    openssl-1.1.1d             |       h516909a_0         2.1 MB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    certifi-2019.11.28         |           py36_0         149 KB  conda-forge
    geopy-1.21.0               |             py_0          58 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1.21.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

In [2]:
from bs4 import BeautifulSoup
import requests
import pandas as pd

In [3]:
#Scrape the list of postal codes of Canada

List_url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
source = requests.get(List_url).text
soup = BeautifulSoup(source, 'xml')
table = soup.find('table')
#table

In [4]:
column_names = ['Postalcode', 'Borough', 'Neighborhood']
df = pd.DataFrame(columns = column_names)
df

Empty DataFrame
Columns: [Postalcode, Borough, Neighborhood]
Index: []

In [5]:
# Search all the postcode, borough, neighborhood in the table
for tr in table.find_all('tr'):
    row_data=[]
    for td in tr.find_all('td'):
        row_data.append(td.text.strip())
    if len(row_data) == 3:
        df.loc[len(df)] = row_data
        
df.head(10)

Postalcode           Borough      Neighborhood
0        M1A      Not assigned      Not assigned
1        M2A      Not assigned      Not assigned
2        M3A        North York         Parkwoods
3        M4A        North York  Victoria Village
4        M5A  Downtown Toronto      Harbourfront
5        M6A        North York  Lawrence Heights
6        M6A        North York    Lawrence Manor
7        M7A  Downtown Toronto      Queen's Park
8        M8A      Not assigned      Not assigned
9        M9A         Etobicoke  Islington Avenue

In [6]:
#Remove unassigned Borough
#df = df[df['Borough'] !=  'Not assigned']
#df.head(10)


# Get names of indexes for which column Borough has value "Not assigned"
indexNames = df[ df['Borough'] =='Not assigned'].index

# Delete these row indexes from dataFrame
df.drop(indexNames , inplace=True)
df.head(10)

Postalcode           Borough      Neighborhood
2         M3A        North York         Parkwoods
3         M4A        North York  Victoria Village
4         M5A  Downtown Toronto      Harbourfront
5         M6A        North York  Lawrence Heights
6         M6A        North York    Lawrence Manor
7         M7A  Downtown Toronto      Queen's Park
9         M9A         Etobicoke  Islington Avenue
10        M1B       Scarborough             Rouge
11        M1B       Scarborough           Malvern
13        M3B        North York   Don Mills North

In [7]:
df.loc[df['Neighborhood'] =='Not assigned' , 'Neighborhood'] = df['Borough']
df.head(10)

Postalcode           Borough      Neighborhood
2         M3A        North York         Parkwoods
3         M4A        North York  Victoria Village
4         M5A  Downtown Toronto      Harbourfront
5         M6A        North York  Lawrence Heights
6         M6A        North York    Lawrence Manor
7         M7A  Downtown Toronto      Queen's Park
9         M9A         Etobicoke  Islington Avenue
10        M1B       Scarborough             Rouge
11        M1B       Scarborough           Malvern
13        M3B        North York   Don Mills North

In [8]:
df_group = df.groupby('Postalcode')['Neighborhood'].apply(lambda x: "%s" % ', '.join(x))
df_group = df_group.reset_index(drop=False)
df_group.rename(columns={'Neighborhood':'Neighborhood_joined'},inplace=True)
df_group.head(10)

Postalcode                              Neighborhood_joined
0        M1B                                   Rouge, Malvern
1        M1C           Highland Creek, Rouge Hill, Port Union
2        M1E                Guildwood, Morningside, West Hill
3        M1G                                           Woburn
4        M1H                                        Cedarbrae
5        M1J                              Scarborough Village
6        M1K      East Birchmount Park, Ionview, Kennedy Park
7        M1L                  Clairlea, Golden Mile, Oakridge
8        M1M  Cliffcrest, Cliffside, Scarborough Village West
9        M1N                      Birch Cliff, Cliffside West

In [9]:
df_merge = pd.merge(df, df_group, on='Postalcode')
df_merge.drop(['Neighborhood'], axis=1, inplace=True)
df_merge.drop_duplicates(inplace=True)
df_merge.rename(columns={'Neighborhood_joined':'Neighborhood'}, inplace=True)
df_merge.head(10)

Postalcode           Borough                      Neighborhood
0         M3A        North York                         Parkwoods
1         M4A        North York                  Victoria Village
2         M5A  Downtown Toronto                      Harbourfront
3         M6A        North York  Lawrence Heights, Lawrence Manor
5         M7A  Downtown Toronto                      Queen's Park
6         M9A         Etobicoke                  Islington Avenue
7         M1B       Scarborough                    Rouge, Malvern
9         M3B        North York                   Don Mills North
10        M4B         East York   Woodbine Gardens, Parkview Hill
12        M5B  Downtown Toronto          Ryerson, Garden District

In [10]:
df_merge.shape

(103, 3)

In [11]:
def get_geocode(postal_code):
    # initialize your variable to None
    lat_lng_coords = None
    while(lat_lng_coords is None):
        g = geocoder.google('{}, Toronto, Ontario'.format(postal_code))
        lat_lng_coords = g.latlng
    latitude = lat_lng_coords[0]
    longitude = lat_lng_coords[1]
    return latitude,longitude

In [12]:
geo_df=pd.read_csv('http://cocl.us/Geospatial_data')
geo_df.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [13]:
geo_df.rename(columns={'Postal Code':'Postalcode'},inplace=True)
geo_merged = pd.merge(geo_df, df_merge, on='Postalcode')
geo_data=geo_merged[['Postalcode','Borough','Neighborhood','Latitude','Longitude']]
geo_data.head()

Postalcode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Rouge, Malvern  43.806686   
1        M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [36]:
# Check coordinates for a couple of neighborhoods
geo_data[(geo_data['Postalcode']=='M5G') |
                             (geo_data['Postalcode']=='M2H') ]

Postalcode           Borough        Neighborhood   Latitude  Longitude
17        M2H        North York   Hillcrest Village  43.803762 -79.363452
57        M5G  Downtown Toronto  Central Bay Street  43.657952 -79.387383

In [37]:
#Export to .CSV
geo_data.to_csv('Toronto_Postcodes_2.csv')

In [38]:
# Read .csv file from above
df = pd.read_csv('Toronto_Postcodes_2.csv', index_col=0)
df.head()

Postalcode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Rouge, Malvern  43.806686   
1        M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [39]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df['Borough'].unique()),
        df.shape[0]
    )
)

The dataframe has 10 boroughs and 103 neighborhoods.


In [40]:
df.rename(columns={'Neighbourhood': 'Neighborhood'}, inplace=True)
#count Bourough and Neighborhood
df.groupby('Borough').count()['Neighborhood']

Borough
Central Toronto      9
Downtown Toronto    19
East Toronto         5
East York            5
Etobicoke           12
Mississauga          1
North York          24
Scarborough         17
West Toronto         6
York                 5
Name: Neighborhood, dtype: int64

In [41]:
df_toronto = df[df['Borough'].str.contains('Toronto')]
df_toronto.reset_index(inplace=True)
df_toronto.drop('index', axis=1, inplace=True)
df_toronto.head()

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


Postalcode          Borough                    Neighborhood   Latitude  \
0        M4E     East Toronto                     The Beaches  43.676357   
1        M4K     East Toronto    The Danforth West, Riverdale  43.679557   
2        M4L     East Toronto  The Beaches West, India Bazaar  43.668999   
3        M4M     East Toronto                 Studio District  43.659526   
4        M4N  Central Toronto                   Lawrence Park  43.728020   

   Longitude  
0 -79.293031  
1 -79.352188  
2 -79.315572  
3 -79.340923  
4 -79.388790

In [42]:
#Check the number of neighborhoods
print(df_toronto.groupby('Borough').count()['Neighborhood'])

Borough
Central Toronto      9
Downtown Toronto    19
East Toronto         5
West Toronto         6
Name: Neighborhood, dtype: int64


In [43]:
#Create list with the Boroughs (to be used later)
boroughs = df_toronto['Borough'].unique().tolist()

In [44]:
#Obtain the coordinates from the dataset itself, just averaging Latitude/Longitude of the current dataset 
lat_toronto = df_toronto['Latitude'].mean()
lon_toronto = df_toronto['Longitude'].mean()
print('The geographical coordinates of Toronto are {}, {}'.format(lat_toronto, lon_toronto))

The geographical coordinates of Toronto are 43.66713498717948, -79.38987324871795


In [45]:
borough_color = {}
for borough in boroughs:
    borough_color[borough]= '#%02X%02X%02X' % tuple(np.random.choice(range(256), size=3)) #Random color

In [46]:
map_toronto = folium.Map(location=[lat_toronto, lon_toronto], zoom_start=12)
# add markers to map
for lat, lng, borough, neighborhood in zip(df_toronto['Latitude'], 
                                           df_toronto['Longitude'],
                                           df_toronto['Borough'], 
                                           df_toronto['Neighborhood']):
    label_text = borough + ' - ' + neighborhood
    label = folium.Popup(label_text)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color=borough_color[borough],
        fill_color=borough_color[borough],
        fill_opacity=0.7).add_to(map_toronto)  
    
map_toronto

# Get venue data from FourSquare

In [14]:
CLIENT_ID = 'YZF0VX05EYPS3S5TT1SQQVTMP33RKZYR2NI42JQDRLFUBSGQ' # your Foursquare ID
CLIENT_SECRET = 'AJOHBFUB2OIRPLVE4HM4SYKGVMUZTEJ4FNNO5GVY0GT0DCAG' # your Foursquare Secret
VERSION = '20180604'

In [15]:
toronto_data=geo_data[geo_data['Borough'].str.contains("Toronto")]
toronto_data.head()

Postalcode          Borough                    Neighborhood   Latitude  \
37        M4E     East Toronto                     The Beaches  43.676357   
41        M4K     East Toronto    The Danforth West, Riverdale  43.679557   
42        M4L     East Toronto  The Beaches West, India Bazaar  43.668999   
43        M4M     East Toronto                 Studio District  43.659526   
44        M4N  Central Toronto                   Lawrence Park  43.728020   

    Longitude  
37 -79.293031  
41 -79.352188  
42 -79.315572  
43 -79.340923  
44 -79.388790

In [16]:
def getNearbyVenues(names, latitudes, longitudes):
    radius=500
    LIMIT=100
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [17]:
toronto_venues = getNearbyVenues(names=toronto_data['Neighborhood'],
                                   latitudes=toronto_data['Latitude'],
                                   longitudes=toronto_data['Longitude']
                                  )


The Beaches
The Danforth West, Riverdale
The Beaches West, India Bazaar
Studio District
Lawrence Park
Davisville North
North Toronto West
Davisville
Moore Park, Summerhill East
Deer Park, Forest Hill SE, Rathnelly, South Hill, Summerhill West
Rosedale
Cabbagetown, St. James Town
Church and Wellesley
Harbourfront
Ryerson, Garden District
St. James Town
Berczy Park
Central Bay Street
Adelaide, King, Richmond
Harbourfront East, Toronto Islands, Union Station
Design Exchange, Toronto Dominion Centre
Commerce Court, Victoria Hotel
Roselawn
Forest Hill North, Forest Hill West
The Annex, North Midtown, Yorkville
Harbord, University of Toronto
Chinatown, Grange Park, Kensington Market
CN Tower, Bathurst Quay, Island airport, Harbourfront West, King and Spadina, Railway Lands, South Niagara
Stn A PO Boxes 25 The Esplanade
First Canadian Place, Underground city
Christie
Dovercourt Village, Dufferin
Little Portugal, Trinity
Brockton, Exhibition Place, Parkdale Village
High Park, The Junction Sout

In [18]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  The Beaches              43.676357              -79.293031   
1  The Beaches              43.676357              -79.293031   
2  The Beaches              43.676357              -79.293031   
3  The Beaches              43.676357              -79.293031   
4  The Beaches              43.676357              -79.293031   

                                Venue  Venue Latitude  Venue Longitude  \
0                   Glen Manor Ravine       43.676821       -79.293942   
1  The Big Carrot Natural Food Market       43.678879       -79.297734   
2                 Grover Pub and Grub       43.679181       -79.297215   
3                   Glen Stewart Park       43.675278       -79.294647   
4                       Upper Beaches       43.680563       -79.292869   

      Venue Category  
0              Trail  
1  Health Food Store  
2                Pub  
3               Park  
4       Neighborhood

In [19]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Adelaide, King, Richmond                                              100   
Berczy Park                                                            56   
Brockton, Exhibition Place, Parkdale Village                           24   
Business Reply Mail Processing Centre 969 Eastern                      17   
CN Tower, Bathurst Quay, Island airport, Harbou...                     16   
Cabbagetown, St. James Town                                            48   
Central Bay Street                                                     82   
Chinatown, Grange Park, Kensington Market                              86   
Christie                                                               18   
Church and Wellesley                                                   86   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             36   
Davisville North                                                        8   
Deer Park, Forest Hill SE, Rathnelly, South Hil...                     16   
Design Exchange, Toronto Dominion Centre                              100   
Dovercourt Village, Dufferin                                           16   
First Canadian Place, Underground city                                100   
Forest Hill North, Forest Hill West                                     4   
Harbord, University of Toronto                                         35   
Harbourfront                                                           48   
Harbourfront East, Toronto Islands, Union Station                     100   
High Park, The Junction South                                          24   
Lawrence Park                                                           3   
Little Portugal, Trinity                                               56   
Moore Park, Summerhill East                                             3   
North Toronto West                                                     22   
Parkdale, Roncesvalles                                                 14   
Queen's Park                                                           41   
Rosedale                                                                4   
Roselawn                                                                2   
Runnymede, Swansea                                                     38   
Ryerson, Garden District                                              100   
St. James Town                                                        100   
Stn A PO Boxes 25 The Esplanade                                        95   
Studio District                                                        44   
The Annex, North Midtown, Yorkville                                    22   
The Beaches                                                             5   
The Beaches West, India Bazaar                                         19   
The Danforth West, Riverdale                                           41   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Adelaide, King, Richmond                                               100   
Berczy Park                                                             56   
Brockton, Exhibition Place, Parkdale Village                            24   
Business Reply Mail Processing Centre 969 Eastern                       17   
CN Tower, Bathurst Quay, Island airport, Harbou...                      16   
Cabbagetown, St. James Town                                             48   
Central Bay Street                                                      82   
Chinatown, Grange Park, Kensington Market                               86   
Christie                                                                18   
Church and Wellesley                

In [20]:
#Number of unique venue categories
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 233 uniques categories.


In [21]:
#print out the list of categories
toronto_venues['Venue Category'].unique()[:100]

array(['Trail', 'Health Food Store', 'Pub', 'Park', 'Neighborhood',
       'Greek Restaurant', 'Cosmetics Shop', 'Italian Restaurant',
       'Ice Cream Shop', 'Yoga Studio', 'Brewery',
       'Fruit & Vegetable Store', 'Pizza Place', 'Bookstore',
       'Restaurant', 'Dessert Shop', 'Juice Bar', 'Bubble Tea Shop',
       'Spa', 'Diner', 'Grocery Store', 'Furniture / Home Store', 'Café',
       'Coffee Shop', 'Bakery', 'Caribbean Restaurant',
       'American Restaurant', 'Frozen Yogurt Shop', 'Liquor Store', 'Gym',
       'Fish & Chips Shop', 'Fast Food Restaurant', 'Sushi Restaurant',
       'Pet Store', 'Steakhouse', 'Burrito Place', 'Movie Theater',
       'Sandwich Place', 'Board Shop', 'Light Rail Station',
       'Intersection', 'Fish Market', 'Gay Bar', 'Cheese Shop',
       'Middle Eastern Restaurant', 'Comfort Food Restaurant',
       'Thai Restaurant', 'Seafood Restaurant', 'Stationery Store',
       'Coworking Space', 'Wine Bar', 'Bar', 'Gym / Fitness Center',
       'Latin

In [22]:
# check if the results contain "Middle Eastern Restaurant"
"Middle Eastern Restaurant" in toronto_venues['Venue Category'].unique()

True

Analyze each neighborhood

In [23]:
# one hot encoding
to_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
to_onehot['Neighborhoods'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [to_onehot.columns[-1]] + list(to_onehot.columns[:-1])
to_onehot = to_onehot[fixed_columns]

print(to_onehot.shape)
to_onehot.head()

(1729, 234)


Neighborhoods  Afghan Restaurant  Airport  Airport Food Court  \
0   The Beaches                  0        0                   0   
1   The Beaches                  0        0                   0   
2   The Beaches                  0        0                   0   
3   The Beaches                  0        0                   0   
4   The Beaches                  0        0                   0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Arts & Crafts Store  Asian Restaurant  \
0             0         0            0                    0                 0   
1             0         0            0                    0                 0   
2             0         0            0                    0                 0   
3             0         0            0                    0                 0   
4             0         0            0                    0                 0   

   Athletics & Sports  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  \
0                   0              0          0           0           0   
1                   0              0          0           0           0   
2                   0              0          0           0           0   
3                   0              0          0           0           0   
4                   0              0          0           0           0   

   Bakery  Bank  Bar  Baseball Stadium  Basketball Stadium  Beach  \
0       0     0    0                 0                   0      0   
1       0     0    0                 0                   0      0   
2       0     0    0                 0                   0      0   
3       0     0    0                 0                   0      0   
4       0     0    0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bistro  \
0                0         0           0                   0       0   
1                0         0           0                   0       0   
2                0         0           0                   0       0   
3                0         0           0                   0       0   
4                0         0           0                   0       0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  \
0           0              0          0         0                     0   
1           0              0          0         0                     0   
2           0              0          0         0                     0   
3           0              0          0         0                     0   
4           0              0          0         0                     0   

   Breakfast Spot  Brewery  Bubble Tea Shop  Building  Burger Joint  \
0               0        0                0         0             0   
1               0        0                0         0             0   
2               0        0                0         0             0   
3               0        0                0         0             0   
4               0        0                0         0             0   

   Burrito Place  Bus Line  Butcher  Café  Cajun / Creole Restaurant  \
0              0         0        0     0                          0   
1              0         0        0     0                          0   
2              0         0        0     0                          0   
3              0         0        0     0                          0   
4              0         0        0     0                          0   

   Camera Store  Candy Store  Caribbean

In [24]:
#Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category
to_grouped = to_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(to_grouped.shape)
to_grouped

(39, 234)


Neighborhoods  Afghan Restaurant  \
0                            Adelaide, King, Richmond           0.000000   
1                                         Berczy Park           0.000000   
2        Brockton, Exhibition Place, Parkdale Village           0.000000   
3   Business Reply Mail Processing Centre 969 Eastern           0.000000   
4   CN Tower, Bathurst Quay, Island airport, Harbo...           0.000000   
5                         Cabbagetown, St. James Town           0.000000   
6                                  Central Bay Street           0.000000   
7           Chinatown, Grange Park, Kensington Market           0.000000   
8                                            Christie           0.000000   
9                                Church and Wellesley           0.011628   
10                     Commerce Court, Victoria Hotel           0.000000   
11                                         Davisville           0.000000   
12                                   Davisville North           0.000000   
13  Deer Park, Forest Hill SE, Rathnelly, South Hi...           0.000000   
14           Design Exchange, Toronto Dominion Centre           0.000000   
15                       Dovercourt Village, Dufferin           0.000000   
16             First Canadian Place, Underground city           0.000000   
17                Forest Hill North, Forest Hill West           0.000000   
18                     Harbord, University of Toronto           0.000000   
19                                       Harbourfront           0.000000   
20  Harbourfront East, Toronto Islands, Union Station           0.000000   
21                      High Park, The Junction South           0.000000   
22                                      Lawrence Park           0.000000   
23                           Little Portugal, Trinity           0.000000   
24                        Moore Park, Summerhill East           0.000000   
25                                 North Toronto West           0.000000   
26                             Parkdale, Roncesvalles           0.000000   
27                                       Queen's Park           0.000000   
28                                           Rosedale           0.000000   
29                                           Roselawn           0.000000   
30                                 Runnymede, Swansea           0.000000   
31                           Ryerson, Garden District           0.000000   
32                                     St. James Town           0.000000   
33                    Stn A PO Boxes 25 The Esplanade           0.000000   
34                                    Studio District           0.000000   
35                The Annex, North Midtown, Yorkville           0.000000   
36                                        The Beaches           0.000000   
37                     The Beaches West, India Bazaar           0.000000   
38                       The Danforth West, Riverdale           0.000000   

    Airport  Airport Food Court  Airport Lounge  Airport Service  \
0    0.0000              0.0000           0.000           0.0000   
1    0.0000              0.0000           0.000           0.0000   
2    0.0000              0.0000           0.000           0.0000   
3    0.0000              0.0000           0.000           0.0000   
4    0.0625              0.0625           0.125           0.1875   
5    0.0000              0.0000           0.000           0.0000   
6    0.0000              0.0000           0.000           0.0000   
7    0.0000              0.0000           0.000           0.0000   
8    0.0000              0.0000           0.000           0.0000   
9    0.0000              0.0000           0.000           0.0000   
10   0.0000              0.0000           0.000           0.0000   
11   0.0000              0.0000           0.000           0.0000   
12   0.0000              0.0000           0.000           0.0000   
13   0.0000              0.0000           0.000

In [25]:
len(to_grouped[to_grouped["Middle Eastern Restaurant"] > 0])

6

In [27]:
#Create a new dataframe to find Middle Eastern Restaurants only
mideast = to_grouped[["Neighborhoods","Middle Eastern Restaurant"]]
mideast.head()

Neighborhoods  \
0                           Adelaide, King, Richmond   
1                                        Berczy Park   
2       Brockton, Exhibition Place, Parkdale Village   
3  Business Reply Mail Processing Centre 969 Eastern   
4  CN Tower, Bathurst Quay, Island airport, Harbo...   

   Middle Eastern Restaurant  
0                        0.0  
1                        0.0  
2                        0.0  
3                        0.0  
4                        0.0

## Cluster Neighborhoods

In [28]:
#Run k-means to cluster the neighborhoods in Toronto into 3 clusters.
# set number of clusters
toclusters = 3

to_clustering = mideast.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=0).fit(to_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 0, 0, 0, 0, 2, 0, 0, 0], dtype=int32)

In [29]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
to_merged = mideast.copy()

# add clustering labels
to_merged["Cluster Labels"] = kmeans.labels_

In [30]:
to_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
to_merged.head()

Neighborhood  \
0                           Adelaide, King, Richmond   
1                                        Berczy Park   
2       Brockton, Exhibition Place, Parkdale Village   
3  Business Reply Mail Processing Centre 969 Eastern   
4  CN Tower, Bathurst Quay, Island airport, Harbo...   

   Middle Eastern Restaurant  Cluster Labels  
0                        0.0               0  
1                        0.0               0  
2                        0.0               0  
3                        0.0               0  
4                        0.0               0

In [31]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
to_merged = to_merged.join(toronto_venues.set_index("Neighborhood"), on="Neighborhood")

print(to_merged.shape)
to_merged.head()

(1729, 9)


Neighborhood  Middle Eastern Restaurant  Cluster Labels  \
0  Adelaide, King, Richmond                        0.0               0   
0  Adelaide, King, Richmond                        0.0               0   
0  Adelaide, King, Richmond                        0.0               0   
0  Adelaide, King, Richmond                        0.0               0   
0  Adelaide, King, Richmond                        0.0               0   

   Neighborhood Latitude  Neighborhood Longitude  \
0              43.650571              -79.384568   
0              43.650571              -79.384568   
0              43.650571              -79.384568   
0              43.650571              -79.384568   
0              43.650571              -79.384568   

                                         Venue  Venue Latitude  \
0  Four Seasons Centre for the Performing Arts       43.650592   
0       The Keg Steakhouse + Bar - York Street       43.649987   
0                                    Rosalinda       43.650252   
0                       Nathan Phillips Square       43.652270   
0                           Shangri-La Toronto       43.649129   

   Venue Longitude                 Venue Category  
0       -79.385806                   Concert Hall  
0       -79.384103                     Restaurant  
0       -79.385156  Vegetarian / Vegan Restaurant  
0       -79.383516                          Plaza  
0       -79.386557                          Hotel

In [32]:
# sort the results by Cluster Labels
print(to_merged.shape)
to_merged.sort_values(["Cluster Labels"], inplace=True)
to_merged

(1729, 9)


Neighborhood  \
0                            Adelaide, King, Richmond   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfro

In [33]:
#Visualize the clusters
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

In [47]:
# create map
map_clusters = folium.Map(location=[lat_toronto, lon_toronto], zoom_start=11)

# set color scheme for the clusters
x = np.arange(toclusters)
ys = [i+x+(i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(to_merged['Neighborhood Latitude'], to_merged['Neighborhood Longitude'], to_merged['Neighborhood'], to_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster))
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [49]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

# Examine clusters

In [50]:
#Cluster 0
to_merged.loc[to_merged['Cluster Labels'] == 0]

Neighborhood  \
0                            Adelaide, King, Richmond   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfro

In [51]:
#Cluster 1
to_merged.loc[to_merged['Cluster Labels'] == 1]

Neighborhood  Middle Eastern Restaurant  \
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
15         Dovercourt Village, Dufferin                   0.062500   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   
35  The Annex, North Midtown, Yorkville                   0.045455   

    Cluster Labels  Neighborhood Latitude  Neighborhood Longitude  \
35               1              43.672710              -79.405678   
35               1              43.672710              -79.405678   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005              -79.442259   
15               1              43.669005             

In [52]:
#Cluster 2
to_merged.loc[to_merged['Cluster Labels'] == 2]

Neighborhood  Middle Eastern Restaurant  Cluster Labels  \
6         Central Bay Street                   0.024390               2   
31  Ryerson, Garden District                   0.030000               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
6         Central Bay Street                   0.024390               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
34           Studio District                   0.022727               2   
6         Central Bay Street                   0.024390               2   
6         Central Bay Street                   0.024390               2   
31  Ryerson, Garden District                   0.030000               2   
31  Ryerson, Garden District                   0.030000               2   
31  Ryerson, Garden District                   0.030000               2   
31  Ryerson, Garden District             

# Conclusion

Most of Middle Eastern restaurants are in Cluster 1 and 2 which is around Studio District, Garden District, Central Bay Street areas. The lowest (close to zero) in Cluster 0 areas which are Adelaide, King, Richmond. Also, there are good opportunities to open near Harbourfront East, Toronto Islands, Union Station as the competition seems to be low. Looking at nearby venues, it seems Cluster 0 might be a good location as there are not a lot of Middle Eastern restaurants in these areas. Therefore, this project recommends the client to open an authentic Middle Eastern restaurant in these locations with little to no competition. Nonetheless, if the food is authentic, affordable and good taste, I am confident that it will have great following everywhere.